In [1]:
# Load symbolicregression model

import json
import torch
import os, sys
import symbolicregression
import sympytorch
import requests
from sympy.core.rules import Transform

model_path = "ckpt/model.pt" 
try:
    if not os.path.isfile(model_path): 
        print("Downloading model...")
        url = "https://dl.fbaipublicfiles.com/symbolicregression/model1.pt"
        r = requests.get(url, allow_redirects=True)
        open(model_path, 'wb').write(r.content)
    if not torch.cuda.is_available():
        sr_model = torch.load(model_path, map_location=torch.device('cpu'))
    else:
        sr_model = torch.load(model_path)
        sr_model = sr_model.cuda()
    print(sr_model.device)
    print("Model successfully loaded!")

except Exception as e:
    print("ERROR: model not loaded! path was: {}".format(model_path))
    print(e)    
    
est = symbolicregression.model.SymbolicTransformerRegressor(
                        model=sr_model,
                        max_input_points=10001,
                        n_trees_to_refine=5,
                        rescale=True
                        )

cuda:0
Model successfully loaded!


In [2]:
#sr_model.env.equation_id2word

In [3]:
import numpy as np
import sympy as sp
from sympy import sympify, lambdify, symbols, integrate, Interval, Symbol, I, S, oo, plot
from IPython.display import display

# Given an expr f (of variable t), returns its integral, together with t's and y's for regression
def integrate_expr(f, min_x=-4.0, max_x=4.0, increment=0.001, verbose=False):
    if verbose:
        print("Running integration on")
        display(f)
    # Compute integration
    x, t = symbols(['x','t'])
    fi = integrate(f, t)
    if verbose:
        display(fi)
        #plot(fi, (t, min_x, max_x))
    # Generate data for symbolic regression
    fl = lambdify((t), fi, "numpy")
    ts = np.arange(min_x, max_x, increment)
    ys = fl(ts)
    return fi, ts, ys
    
integrate_expr(sympify("2*t**2-t*2+2.5"), verbose=True)

Running integration on


2*t**2 - 2*t + 2.5

0.666666666666667*t**3 - 1.0*t**2 + 2.5*t

(0.666666666666667*t**3 - 1.0*t**2 + 2.5*t,
 array([-4.   , -3.999, -3.998, ...,  3.997,  3.998,  3.999]),
 array([-68.66666667, -68.62417567, -68.58170266, ...,  36.58722965,
         36.61369466,  36.64017367]))

In [4]:
from utils.utils import *

def round_expr(expr, num_digits=2):
    return expr.xreplace(Transform(lambda x: x.round(num_digits), lambda x: isinstance(x, sp.Float)))

# Run symbolic regression on given data
# Returns: (raw regressed expr, rounded expr, model refined expr)
@timeout(15)
def symbolic_regress(sr_model, xs, ys, generate_refinement=False, verbose=False):
    if verbose:
        print("Running Symbolic Regression...")
    ##Example of data
    xs = np.reshape(xs, (len(xs),1))
    ys = np.reshape(ys, (len(ys),1))
    sr_model.fit(xs,ys)
    #
    replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
    model_str = sr_model.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
    for op,replace_op in replace_ops.items():
        model_str = model_str.replace(op,replace_op)
    #
    raw_expr = sp.parse_expr(model_str)
    x_0, t = symbols(['x_0', 't'])
    raw_expr = raw_expr.subs(x_0, t)
    if verbose:
        display(raw_expr)
    #
    expr = sp.expand(raw_expr)
    rounded_expr = round_expr(expr)
    if verbose:
        display(rounded_expr)
    #
    # Encode some input text
    if generate_refinement:
        prompt = str(rounded_expr)
        input_ids = tokenizer.encode(prompt, return_tensors='pt')
        #
        # Generate text
        output = model.generate(input_ids, max_length=50, num_return_sequences=1, temperature=0.1)
        #
        # Decode and print the output
        generated_text = tokenizer.decode(output[0], skip_special_tokens=True)
        generated_expr = sympify(generated_text)
        if verbose:
            display(generated_expr)
        #
    else:
        generated_expr = None
    return raw_expr, rounded_expr, generated_expr


fi, ts, ys = integrate_expr(sympify("1.5*cos(-2.3*t)+1"), verbose=False)
rounded_fi = round_expr(fi)
display(rounded_fi)
raw_expr, rounded_expr, generated_expr = symbolic_regress(est, ts, ys, verbose=False)
display(raw_expr)
display(rounded_expr)

print("Diff1:")
display(rounded_fi-rounded_expr)
# print("Diff2:")
# display(rounded_fi-generated_expr)

t + 0.65*sin(2.3*t)

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')


1.0015801516273977*t + 0.6502496605248392*sin(2.3040611844449385*t + 0.012651715497814755) + 0.0034417706500794442

1.0*t + 0.65*sin(2.3*t + 0.01)

Diff1:


0.65*sin(2.3*t) - 0.65*sin(2.3*t + 0.01)

In [5]:
import random

template = "c_0*f_0(c_1*t)+c_2"

functions = ['sin', 'cos', 'exp']

def random_constant():
    if random.random() < 0.33:
        return 1
    while True:
        if random.random() < 0.5:
            val = random.randint(-5, 5)
        else:
            val = round(random.uniform(-5.0, 5.0), 1)
        return val

def generate_non_poly_expr():
    func = random.choice(functions)
    while True:
        c_0 = random_constant()
        if c_0 != 0:
            break
    c_1 = random_constant()
    if random.random() < 0.33:
        c_2 = random_constant()
    else:
        c_2 = 0
    expr = template.replace('f_0', str(func)).replace('c_0', str(c_0)).replace('c_1', str(c_1)).replace('c_2', str(c_2))
    return sp.simplify(sympify(expr))

for i in range(10):
    display(generate_non_poly_expr())

cos(4*t) - 5

-4.3*sin(5*t)

-0.8*cos(1.5*t)

0.7*sin(t)

sin(4*t)

-2.2*sin(t)

sin(4*t)

4.9*sin(t)

3.8*exp(3.0*t)

0.7*sin(t)

In [6]:
exprs = []
for i in range(20000):
    exprs.append(generate_non_poly_expr())

print(len(exprs))

20000


In [ ]:
# Run symbolic regression on each case
import json

seen_exprs = set()
fin = open("../datasets/parametric_equations_randomized_nonpoly_integral_results.json", "r")
lines = fin.readlines()
for line in lines:
    result = json.loads(line)
    expr = result["original"]
    seen_exprs.add(expr)
fin.close()
print(f"{len(seen_exprs)} exprs loaded")

fout = open("../datasets/parametric_equations_randomized_nonpoly_integral_results.json", "a")
num_seen = 0
num_seen_changed = False

for f in exprs:
    if str(f) in seen_exprs:
        num_seen+=1
        num_seen_changed = True
        continue
    else:
        num_seen_changed = False
    if num_seen_changed:
        print(f"{num_seen} exprs ignored")
    #print("Original expr and its integral:")
    #display(f)
    #print(f)
    try:
        fi, xs, ys = integrate_expr(f, verbose=False)
        x, t = symbols(['x','t'])
        fi = fi.subs({x:t})
        rounded_fi = round_expr(fi)
        #display(rounded_fi)
        raw_expr, rounded_expr, generated_expr = symbolic_regress(est, xs, ys, generate_refinement=False, verbose=False)
#         print("Generated expr:")
#         display(generated_expr)
        results = {"original":str(f),
                   "integral":str(fi),
                   "rounded_integral":str(rounded_fi),
                   "regressed":str(raw_expr),
                   "rounded_regressed":str(rounded_expr),
                   #"generated_regressed":str(generated_expr),
                   "diff_rounded": str(rounded_fi-rounded_expr),
                   #"diff_generated": str(rounded_fi-generated_expr)
                  }
        fout.write(json.dumps(results))
        fout.write('\n')
        fout.flush()
    except Exception as e:
        print("Failed to run symbolic regression")
        print(e)
        continue
    #     print("Diff1:")
    #     display(rounded_fi-rounded_expr)
    #     print("Diff2:")
    #     display(rounded_fi-generated_expr)

fout.close()

4347 exprs loaded


/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

Failed to run symbolic regression
object of type 'int' has no len()


...

Failed to run symbolic regression
Invalid comparison of non-real zoo


/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('grad')
/home/mcwave/anaconda3/envs/symbolic/lib/python3.10/site-packages/torch/_functorch/deprecated.py:62: UserWarning: We've integrated functorch into PyTorch. As the final step of the integration, functorch.grad is deprecated as of PyTorch 2.0 and will be deleted in a future version of PyTorch >= 2.3. Please use torch.func.grad instead; see the PyTorch 2.0 release notes and/or the torch.func migration guide for more details https://pytorch.org/docs/master/func.migrating.html
  warn_deprecated('gra

In [ ]:
f = exprs[0]
display(f)

fi, xs, ys = integrate_expr(f, verbose=False)
x, t = symbols(['x','t'])
fi = fi.subs({x:t})
rounded_fi = round_expr(fi)
display(rounded_fi)

raw_expr, rounded_expr, generated_expr = symbolic_regress(est, xs, ys, generate_refinement=False, verbose=False)

In [ ]:
display(rounded_expr)

In [ ]:
# Check the accuracy of symbolic regression

import json
from sympy import evalf, N
from utils.utils import *


# Check if f1 and f2 are almost equal.
# Note: Relative error is defined based on f1. Please use the original expression as f1.
def almost_equal(f1, f2, max_abs_error=0.011, max_relative_error=0.011, verbose=False):
    expr = f1-f2
    coeff_pairs = None
    try:
        coeff_pairs = get_coefficients_and_exponents(expr)
    except:
        print("Cannot get_coefficients_and_exponents")
        print(str(expr))
    if coeff_pairs is None:
        constants = get_all_constants(expr)
    else:
        constants = [p[0] for p in coeff_pairs]
    # Check if all diffs are within max_abs_error
    violators = [c for c in constants if c == sp.nan or abs(c) > max_abs_error]
    if verbose:
        print("Violating constants:", violators)
    if len(violators) == 0:
        return True
    # Check if all violating diffs are within max_relative_error
    try:
        coeffs1 = get_polynomial_coeffs(f1)
        coeffs2 = get_polynomial_coeffs(f2)
    except:
        return False
    for i in range(len(coeffs1)):
        if abs(coeffs1[i] - coeffs2[i]) > max_abs_error and \
           abs(coeffs1[i] - coeffs2[i]) > max_relative_error*abs(coeffs1[i]):
            return False
    return True
    

# fin = open("datasets/parametric_equations_polynomial_integral_results.json", "r")
# lines = fin.readlines()

# num_total, qualified_rounded, qualified_generated = 0, 0, 0
# for line in lines:
#     result = json.loads(line)
#     if "diff_rounded" not in result or "diff_generated" not in result:
#         continue
#     rounded_integral = N(sympify(result["rounded_integral"]))
#     rounded_regressed = N(sympify(result["rounded_regressed"]))
# #     display(rounded_integral)
# #     display(rounded_regressed)
#     try:
#         rounded_regressed = filter_non_polynomial(rounded_regressed)
#     except:
#         print("Cannot filter non-polynomials on", str(rounded_regressed))
#     #generated_regressed = N(sympify(result["generated_regressed"]))
#     diff_rounded = rounded_integral - rounded_regressed
#     #diff_generated = sympify(result["diff_generated"])
#     num_total += 1
#     if almost_equal(rounded_integral, rounded_regressed, verbose=False):
#         qualified_rounded += 1
#     else:
#         display(rounded_integral)
#         display(rounded_regressed)
#         print(rounded_regressed)
#         display(diff_rounded)
# #     if is_close_to_zero(diff_generated, True):
# #         qualified_generated += 1
    
# fin.close()

# print(num_total, qualified_rounded, qualified_generated)

In [ ]:
# for i in range(1000):
#     f = originals[i]
#     x, t = symbols(['x','t'])
#     fi = integrate(f, t)
#     g = integrals[i]
#     #fs, gs, diff = get_diff(fi, g, t)
#     # print(np.mean(np.abs(fs)))
#     # print(np.mean(np.abs(gs)))
#     # print(np.mean(np.abs(diff)))
#     relative_diff = get_avg_diff(fi, g, t)
#     if relative_diff > 0.01:
#         print("CASE", i)
#         display(fi)
#         display(g)
#         print(relative_diff)

In [ ]:
# Generate data for regression to infer the rules for integral
# The data is in the following format:
# Let us suppose there are N regression problems, and MAX_POWER=6, which is 
#   the highest power allowed in our polynomials.
#   data_series is a list of 7 items, each corresponding to a particular power
#   Each item is a tuple of 2 elements, with the first being x's and the second
#   being y's for the regression problem for the corresponding power.
#   The y's is a 1-D array of size N, which is the coefficient of that particular power for
#   each of N regression problems.
#   The each of the x's is an array of size 14, which contains 
#   [0, coeff-power-0, 1, coeff-power-1, 2, coeff-power-2, ...]
# If we want to find the connection between x's and y's, we should find that
#   y_1 = x_1 (coeff-power-0)
#   y_2 = x_3 (coeff-power-1)
#   y_3 = x_5 (coeff-power-2)
#   y_4 = x_7 (coeff-power-3)
#   y_5 = x_9 (coeff-power-4)

from sympy import evalf, N
from utils.utils import *

fin = open("datasets/parametric_equations_polynomial_integral_results.json", "r")
lines = fin.readlines()

MAX_POWER = 6
MAX_AVG_DIFF = 0.01

data_series = [([],[])] * (MAX_POWER+1)
data_series = []
originals = []
integrals = []
t = Symbol('t')

for i in range(MAX_POWER+1):
    data_series.append((list(),list()))

for line in lines:
    result = json.loads(line)
    if "rounded_regressed" not in result:
        continue
    original = N(sympify(result["original"]))
    integral = N(sympify(result["rounded_regressed"]))
    try:
        original = filter_non_polynomial(original)
        integral = filter_non_polynomial(integral)
        original_integral = integrate(original, t)
        avg_diff = get_avg_diff(original_integral, integral, t)
        if avg_diff > MAX_AVG_DIFF:
            print("Skipping due to diff=", avg_diff)
            display(original_integral)
            display(integral)
            continue
    except:
        print("Cannot filter non-polynomials on", str(integral))
        continue
    try:
        coeffs_original = get_polynomial_coeffs(original)
        coeffs_integral = get_polynomial_coeffs(integral)
    except:
        print("Cannot get_coefficients_and_exponents")
        display(integral)
        continue
    if original.is_constant():
        print("Skipping", line)
        continue
    xs = list()
    for i in range(MAX_POWER+1):
        xs.append(i)
        xs.append(coeffs_original[i])
    for i in range(MAX_POWER+1):
        data_series[i][0].append(xs.copy())
        data_series[i][1].append(coeffs_integral[i])
    if len(data_series[0][1]) % 100 == 0:
        print(len(data_series[0][1]), "processed")
#     if len(data_series[0][1]) == 3844:
#         display(original)
#         print(original.is_constant())
#         display(sympify(result["original"]))
#         display(integral)
    originals.append(original)
    integrals.append(integral)
    
fin.close()


In [ ]:
import pickle

# fout = open('/tmp/test_data_series.pkl', 'wb')
# pickle.dump(data_series, fout)
# fout.close()

fin = open('/tmp/test_data_series.pkl', 'rb')
data_series = pickle.load(fin)
fin.close()

# Check if the results are as expected
n = len(data_series[1][1])
for y_idx in range(3, 4):
    xs = np.asarray(data_series[y_idx][0])
    x1s = xs[:,(y_idx-1)*2+1]
    ys = data_series[y_idx][1]
    for i in range(n):
        if abs(ys[i] - x1s[i]/y_idx) > 0.02 and abs(ys[i]/(x1s[i]/y_idx)-1) > 0.02:
            print(f"y_idx={y_idx}, i={i}, x={x1s[i]}, y={ys[i]}")
            display(originals[i])
            display(integrals[i])

In [ ]:
y_idx=1

n = len(data_series[1][1])

est_simple = symbolicregression2.model.SymbolicTransformerRegressor(
                        model=sr_model,
                        max_input_points=10001,
                        n_trees_to_refine=100,
                        rescale=True
                        )


xs = np.asarray(data_series[y_idx][0])
x1s = np.reshape(xs[:,y_idx], (n,1))
ys = np.reshape(data_series[y_idx][1], (n,1))
ys = ys + 2*x1s*x1s + 3.5

print(xs[0:10, y_idx])
print(ys[0:10])

est_simple.fit(x1s,ys)

replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
model_str = est_simple.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
for op,replace_op in replace_ops.items():
    model_str = model_str.replace(op,replace_op)
    
print(model_str)

raw_expr = sp.parse_expr(model_str)
sp.simplify(sp.expand(round_expr(raw_expr)))

In [ ]:
y_idx=2
n = len(data_series[1][1])

xs = np.asarray(data_series[y_idx][0])
x3s = np.reshape(xs[:,2*y_idx+1], (n,1))
ys = np.reshape(data_series[y_idx][1], (n,1))
ys = ys + 2*x3s*x3s + 3.5

# print(xs[0:10, 1])
# print(ys[0:10])

est_simple.fit(x3s,ys)

replace_ops = {"add": "+", "mul": "*", "sub": "-", "pow": "**", "inv": "1/"}
model_str = est_simple.retrieve_tree(with_infos=True)["relabed_predicted_tree"].infix()
for op,replace_op in replace_ops.items():
    model_str = model_str.replace(op,replace_op)
    
print(model_str)

raw_expr = sp.parse_expr(model_str)
sp.simplify(sp.expand(round_expr(raw_expr)))

In [ ]:
import scipy

y_idx=1
ys = np.asarray(data_series[y_idx][1])
xs = np.asarray(data_series[y_idx][0])[:,1]

print(scipy.stats.linregress(xs, ys))

diff = (ys-xs).flatten()
for i in range(len(diff)):
    if abs(diff[i]) > 0.02:
        print(i, diff[i])

In [ ]:
originals[4]